# Загрузка моделей

In [1]:
import time
import torch
import random
import warnings
import traceback
import numpy as np
import pandas as pd
import IPython.display as ipd
from tqdm import tqdm
from scipy import stats

warnings.filterwarnings('ignore', category=UserWarning)

In [2]:
# Модель с возможностью контроля ударений только на славянских языках
model_ns, _ = torch.hub.load(repo_or_dir='snakers4/silero-models',
                             model='silero_tts',
                             language='ru',
                             speaker='v5_cis_base_nostress',
                             force_reload=True)

# Модель с возможностью контроля ударений на всех языках
model_s, _ = torch.hub.load(repo_or_dir='snakers4/silero-models',
                            model='silero_tts',
                            language='ru',
                            speaker='v5_cis_base',
                            force_reload=True)

# Старая модель на кириллице
old_model, _ = torch.hub.load(repo_or_dir='snakers4/silero-models',
                              model='silero_tts',
                              language='cyrillic',
                              speaker='v4_cyrillic',
                              force_reload=True)

assert model_ns.speakers == model_s.speakers
lang2name ={'bak': 'Башкирский', 'chv': 'Чувашский', 'kaz': 'Казахский', 'kjh': 'Хакасский', 'sah': 'Якутский', 'tat': 'Татарский', 'udm': 'Удмуртский', 'ukr': 'Украинский', 'uzb': 'Узбекский', 'xal': 'Калмыцкий', 'ru': 'Русский',
            'erz': 'Эрзянский', 'bel': 'Белорусский', 'aze': 'Азербайджанский', 'kir': 'Киргизский', 'mdf': 'Мокшанский', 'tgk': 'Таджикский', 'hye': 'Армянский', 'kat': 'Грузинский', 'kbd': 'Кабардино-Черкесский'}
# TODO
langs = ['bak', 'ru', 'tat', 'erz', 'bel', 'udm', 'chv', 'kat', 'aze_lat', 'ukr', 'kjh', 'xal', 'kir', 'mdf', 'tgk', 'uzb_cyr', 'hye', 'kaz', 'sah', 'kbd']
lang_acc = {'uzb_cyr': 'uzb', 'aze_lat': 'aze'}

speakers2lang = {s: s.split('_')[0] for s in model_ns.speakers}

lang2speakers = {}
for speaker, lang in speakers2lang.items():
    lang_name = lang2name[lang]
    (lang2speakers.setdefault(lang_name, [])).append(speaker)

Downloading: "https://github.com/snakers4/silero-models/zipball/master" to /home/keras/.cache/torch/hub/master.zip
100%|█████████████████████████████████████████████████████████████████████████████████████████████| 87.5M/87.5M [00:11<00:00, 8.32MB/s]
Downloading: "https://github.com/snakers4/silero-models/zipball/master" to /home/keras/.cache/torch/hub/master.zip
100%|█████████████████████████████████████████████████████████████████████████████████████████████| 87.4M/87.4M [00:14<00:00, 6.29MB/s]
Downloading: "https://github.com/snakers4/silero-models/zipball/master" to /home/keras/.cache/torch/hub/master.zip
100%|█████████████████████████████████████████████████████████████████████████████████████████████| 33.8M/33.8M [00:06<00:00, 5.40MB/s]


In [3]:
from silero_stress import load_accentor
from silero_stress.simple_accentor import SimpleAccentor

accentors = {}
for lang in langs:
    if lang in ['ru', 'bel', 'ukr']:
        accentor = load_accentor(lang)
    else:
        accentor = SimpleAccentor(lang=lang)
    accentors[lang] = accentor
accentors['aze'] = accentors['aze_lat']
accentors['uzb'] = accentors['uzb_cyr']

In [4]:
def mean_with_moe(data, confidence=0.95):
    a = np.array(data)
    n = len(a)
    mean = np.mean(a)
    sem = stats.sem(a)
    moe = sem * stats.t.ppf((1 + confidence)/2, n-1)  # Margin of error
    return f"{mean:.2f} ± {moe:.2f}"

# Тестирование объективных характеристик

## Тестирование скорости

In [5]:
class Sizing():
    def __init__(self,
                 model,
                 device='cpu',
                 sr=48000,
                 hparams_path=None,
                 measure_part_time=False):
        self.device = device
        assert self.device in ['cuda', 'cpu']
        self.sr = sr
        self.measure_part_time = measure_part_time
        if hparams_path is not None:
            self.load_hparams(hparams_path)
        self.load_model(model)


    def load_model(self, model):
        pass


    def load_hparams(self, hparams_path):
        pass


    def process_model_time(self, text):
        with torch.no_grad():
            text_args = self.prepare_text(text)
            st_t = time.time()
            if self.measure_part_time:
                audio, part_time = self.run_model(*text_args)
            else:
                audio = self.run_model(*text_args)
                part_time = None
            full_t = time.time() - st_t
        return audio, full_t, part_time


    def measure_stats(self, texts, num_threads=8):
        torch._C._jit_set_profiling_mode(False)
        torch.set_num_threads(num_threads)
        synt_times = []
        audio_lens = []
        cuda_vram = []
        part_times = []
        for text in tqdm(texts):
            try:
                audio, full_t, part_time = self.process_model_time(text)
            except KeyboardInterrupt:
                raise KeyboardInterrupt
            except:
                print(trace)
                full_t = 0
                audio_len = 0
            synt_times.append(full_t)
            audio_len = len(audio)/self.sr
            audio_lens.append(audio_len)
            part_times.append(part_time)
            if self.device == 'cuda':
                free_vram, full_vram = torch.cuda.mem_get_info()
                cuda_vram.append(full_vram - free_vram)
                torch.cuda.empty_cache()
        nz_audio_lens = [al for al in audio_lens if al > 0]
        nz_synt_times = [st for st in synt_times if st > 0]
        return synt_times, audio_lens, cuda_vram, part_times


    def run_save_results(self, df, num_threads=8):
        assert 'text' in df.columns
        synt_times, audio_lens, cuda_vram, part_times = self.measure_stats(df.text.values, num_threads)
        df['synt_time'] = synt_times
        df['audio_len'] = audio_lens
        df['thr'] = num_threads
        df['sample_rate'] = self.sr
        df['device'] = self.device
        if self.measure_part_time:
            df['part_time'] = part_times
        if self.device == 'cuda':
            df['cuda_vram'] = cuda_vram
        return df


class DefaultSizing(Sizing):
    def load_model(self, model):
        self.model = model
        # check
        self.run_model('Мен балалық шақта жаңа досдармен танысуды әбден ұнататынмын.',
                       speaker=self.model.speakers[0])

    def prepare_text(self, text):
        speaker = self.model.speakers[0]  # 'bak_alfia'
        return text, speaker

    def run_model(self, text, speaker):
        audio = self.model.apply_tts(text=text,
                                     speaker=speaker,
                                     sample_rate=self.sr,)
        return audio

In [6]:
df = pd.read_csv('files/tts_speed_check_test_add_nostress.csv')

In [7]:
for thr in [4, 1]:
    RTSer = DefaultSizing(device='cpu',
                          model=model_ns)
    rts_df = RTSer.run_save_results(df,
                                    num_threads=thr)
    rts_df['rts'] = rts_df['audio_len']/rts_df['synt_time']
    print(f'Средний RTS({thr} thr): ', rts_df['rts'].agg(mean_with_moe))

100%|████████████████████████████████████████████████████████████████████████████████████████████████| 500/500 [00:31<00:00, 15.65it/s]


Средний RTS(4 thr):  88.45 ± 2.06


100%|████████████████████████████████████████████████████████████████████████████████████████████████| 500/500 [01:20<00:00,  6.21it/s]

Средний RTS(1 thr):  36.09 ± 0.56


## Поддержка SSML

In [8]:
ssml_texts = {
    # русский
    'ru': """<speak>Когда я просыпаюсь,
        <prosody rate="x-slow">я говор+ю довольно медленно</prosody>. Потом я начинаю говорить своим обычным голосом,
        <prosody pitch="x-high"> а могу говорить тоном выше </prosody>,
        или <prosody pitch="x-low">наоборот, ниже</prosody>.
        Потом, если повезет – <prosody rate="fast">я могу говорить и довольно быстро.</prosody>
        А еще я умею делать паузы любой длины, например две секунды <break time="2000ms"/>.
        <p>
        Также я умею делать паузы между параграфами.
        </p>
        <s>И также я умею делать паузы между предложениями</s>
        <s>Вот например как сейчас</s>
        </speak>""",
    # армянский
    'hye': """<speak>Գերեվարվածների <prosody rate="fast">թվի մասին հարցին ի պատասխան'</prosody> նա նշեց,<break time="1000ms"/> որ տարբեր տվյալներ են գալիս, հստակ թիվ նշել չի կարող.</speak>""",
    # азербайджанский(латиница)
    'aze': """<speak>o, <prosody rate="slow">musiqini rusiyada <break time="1500ms"/> möhtəşəm bir orkestrə yazmaq</prosody> istəyir.</speak>""",
    # грузинский
    'kat': """<speak>რატომ გადაწყვიტა <s> პარლამენტის წევრმა - კობა ნაკაიძემ ბრალდებულების</s> მხარდაჭერა და ერთ-ერთი<break time="1200ms"/> მათგანისთვის.</speak>""",
    # узбекский(латиница)
    'uzb': """<speak><prosody pitch="high">Aziz do'stim,</prosody> sizni ko'rib juda xursandmiz,<break time="1000ms"/> o'tiring, choy iching, xush kelibsiz!</speak>"""}

sample_rate = 48000

In [ ]:
# Пример работы

speaker = 'ru_zhadyra'
ssml_text = accentors['ru'](ssml_texts['ru'])
audio = model_ns.apply_tts(ssml_text=ssml_text,
                           speaker=speaker,
                           sample_rate=sample_rate)

print('Русский')
ipd.display(ipd.Audio(audio, rate=sample_rate))

Русский


In [10]:
for lang in ['ru', 'hye', 'aze', 'kat', 'uzb']:
    # выбираем случайного спикера
    speaker = random.choice(lang2speakers[lang2name[lang]])
    ssml_text = ssml_texts[lang]
    if lang == 'ru':
        ssml_text = accentors[lang](ssml_text)
    audio = model_ns.apply_tts(ssml_text=ssml_text,
                               speaker=speaker,
                               sample_rate=sample_rate)
    print(f"Язык: {lang2name[lang]}, диктор: {speaker}")
    ipd.display(ipd.Audio(audio, rate=sample_rate))

Язык: Русский, диктор: ru_kermen


Язык: Армянский, диктор: hye_zara


Язык: Азербайджанский, диктор: aze_gamat


Язык: Грузинский, диктор: kat_vika


Язык: Узбекский, диктор: uzb_saida


## Поддержка разных частот дискретизации

In [11]:
example_text = 'Мен балалық шақта жаңа досдармен танысуды әбден ұнататынмын.'
speaker = 'kaz_zhadyra'
lang = 'kaz'

In [12]:
for sample_rate in [8000, 24000, 48000]:
    audio = model_ns.apply_tts(text=example_text,
                               speaker=speaker,
                               sample_rate=sample_rate)
    print(sample_rate)
    ipd.display(ipd.Audio(audio, rate=sample_rate))

8000


24000


48000


## Автоматическая расстановка ударений

In [13]:
val_df = pd.read_csv('files/langs_val_100texts.csv')

val_df['text'] = val_df['text'].apply(lambda x: x.replace('+', ''))  # Точно без ударений

In [14]:
from silero_stress import load_accentor
from silero_stress.simple_accentor import SimpleAccentor

In [15]:
for lang in langs:
    if lang in ['ru', 'bel', 'ukr']:
        accentor = load_accentor(lang)
    else:
        accentor = SimpleAccentor(lang=lang)

    acc_lang = lang_acc.get(lang, lang)
    texts = val_df[val_df.lang==acc_lang].sample(5).text.values
    print(lang)
    print()
    for text in texts:
        print(text, '->', accentor(text))
    print()

bak

беҙгә саҡ ҡына эш ҡалдырып, апайымдар тағы һыуға китә. -> беҙг+ә с+аҡ ҡын+а +эш ҡалдыр+ып, апайымд+ар тағ+ы һыуғ+а кит+ә.
һеҙҙең эш - уның кәйефен күтәреп, ҡулындағы ҡырынғысты -> һеҙҙ+ең +эш - ун+ың кәйеф+ен күтәр+еп, ҡулындағ+ы 
ә һин, малай, урыныңдан ҡуҙғалма. -> +ә һ+ин, мал+ай, урыныңд+ан ҡуҙғалм+а.
был хәбәрҙе уйлап сығарғанһың, ни өсөн башҡалар был хаҡта белмәй? -> б+ыл хәбәрҙ+е уйл+ап сығарғанһ+ың, н+и өс+өн башҡал+ар б+ыл хаҡт+а белм+әй?
бәрәстәр түңәрәк яһап әйләнәләр, кәзә уртала йырлай. -> бәрәст+әр түңәр+әк яһ+ап әйләнәл+әр, кәз+ә уртал+а йырл+ай.

ru

она ужасно разозлилась: посмотри, как он отощал! -> он+а уж+асно разозл+илась: посмотр+и, к+ак +он отощ+ал!
а потом опять шли сплошные двойки. даже по литературе. -> +а пот+ом оп+ять шл+и сплошн+ые дв+ойки. д+аже п+о литерат+уре.
я в футбол до сих пор играю, не унимался жбанков. -> +я в футб+ол д+о с+их п+ор игр+аю, н+е уним+ался жбанк+ов.
благодарю вас. не за что. -> благодар+ю в+ас. н+е з+а чт+о.
литературные чиновни

sah

үлэ олоҕу тупсарар, сайыннарар. -> үл+э олоҕ+у тупсар+ар, сайыннар+ар.
дьарыгым туруга быйыл соччото суох диэн билиниэхпин наада. -> дьарыг+ым туруг+а бый+ыл соччот+о су+ох ди+эн билини+эхпин наад+а.
лиза салыбырас буолбут илиитинэн бакыаттаах суругу хаба тардан ылла. -> лиз+а салыбыр+ас бу+олбут или+итинэн бакыатта+ах суруг+у хаб+а тард+ан ылл+а.
иэдэһинэн хараҕын уута мөлбөрүйэн сүүрбүтэ. -> иэдэһин+эн хараҕ+ын уут+а мөлбөрүй+эн сүүрбүт+э.
тылынан ситэрэн тиэрдибэт дьиктитин. -> тылын+ан ситэр+эн ти+эрдибэт дьиктит+ин.

kbd

сыт абы гъэщiэгъуэнагъыу хэлъыр?! -> с+ыт аб+ы гъэщiэгъуэнагъы+у хэлъ+ыр?!
дэкiуейти гъащiэм и пкiэлъейм. -> дэкiуейт+и гъащi+эм +и пкiэлъ+ейм.
хэкупсэу щiэблэр къэгъэхъунымкiэ хэкiыпiэфiхэр зэрыщыiэр къыхегъэщ хъусен. -> хэк+упсэу щiэбл+эр къэгъэхъунымкi+э хэкiыпiэфiх+эр зэрыщыi+эр къыхегъ+эщ хъус+ен.
мыр пщiыхьэпiэу илъэгъуагъэнщ. -> м+ыр пщiыхьэпiэ+у илъэгъуагъ+энщ.
щхьэ банапкъэм сыщыбулъэпцiа? -> щхь+э бан+апкъэм сыщыбулъэпцi+а?



In [16]:
# Звучание без ударений

lang = 'bel'
speaker = random.choice(lang2speakers[lang2name[lang]])
print(speaker)

text = val_df[val_df.lang==lang].sample().text.iloc[0]
print('Без ударений:', text)

audio = model_s.apply_tts(text=text,
                          speaker=speaker)
ipd.display(ipd.Audio(audio, rate=48000))

text = accentors[lang](text)
print('С ударениями:', text)

audio = model_s.apply_tts(text=text,
                          speaker=speaker)
ipd.display(ipd.Audio(audio, rate=48000))

bel_larisa
Без ударений: маўляў, у яе падтанцоўка добрая.


С ударениями: маўл+яў, +у я+е падтанц+оўка д+обрая.


# Тестирование качества

Обратите внимание, что в силу особенностей реализации модели UTMOS результаты могут незначительно отличаться друг от друга при повторных прогонах.

In [17]:
# From https://github.com/tarepan/vocos-official/blob/main/metrics/UTMOS.py

import os
import fairseq
import pytorch_lightning as pl
import requests
import torch
import torch.nn as nn
import torchaudio
from tqdm import tqdm

UTMOS_CKPT_URL = "https://huggingface.co/spaces/sarulab-speech/UTMOS-demo/resolve/main/epoch%3D3-step%3D7459.ckpt"
WAV2VEC_URL = "https://huggingface.co/spaces/sarulab-speech/UTMOS-demo/resolve/main/wav2vec_small.pt"

"""
UTMOS score, automatic Mean Opinion Score (MOS) prediction system, 
adapted from https://huggingface.co/spaces/sarulab-speech/UTMOS-demo
"""


class UTMOSScore:
    """Predicting score for each audio clip."""

    def __init__(self, device, ckpt_path="epoch=3-step=7459.ckpt"):
        self.device = device
        filepath = ckpt_path
        if not os.path.exists(filepath):
            download_file(UTMOS_CKPT_URL, filepath)
        self.resampler = torchaudio.transforms.Resample(
            orig_freq=48000, # default tts sr
            new_freq=16000,
            resampling_method="sinc_interpolation",
            lowpass_filter_width=6,
            dtype=torch.float32,
        ).to(device)
        self.model = BaselineLightningModule.load_from_checkpoint(filepath).eval().to(device)

    def score(self, wavs: torch.tensor) -> torch.tensor:
        """
        Args:
            wavs: audio waveform to be evaluated. When len(wavs) == 1 or 2,
                the model processes the input as a single audio clip. The model
                performs batch processing when len(wavs) == 3.
        """
        if len(wavs.shape) == 1:
            out_wavs = wavs.unsqueeze(0).unsqueeze(0)
        elif len(wavs.shape) == 2:
            out_wavs = wavs.unsqueeze(0)
        elif len(wavs.shape) == 3:
            out_wavs = wavs
        else:
            raise ValueError("Dimension of input tensor needs to be <= 3.")
        out_wavs = self.resampler(out_wavs)
        bs = out_wavs.shape[0]
        batch = {
            "wav": out_wavs,
            "domains": torch.zeros(bs, dtype=torch.int).to(self.device),
            "judge_id": torch.ones(bs, dtype=torch.int).to(self.device) * 288,
        }
        with torch.no_grad():
            output = self.model(batch)

        return output.mean(dim=1).squeeze(1).cpu().detach() * 2 + 3


def download_file(url, filename):
    """
    Downloads a file from the given URL

    Args:
        url (str): The URL of the file to download.
        filename (str): The name to save the file as.
    """
    print(f"Downloading file {filename}...")
    response = requests.get(url, stream=True)
    response.raise_for_status()

    total_size_in_bytes = int(response.headers.get("content-length", 0))
    progress_bar = tqdm(total=total_size_in_bytes, unit="iB", unit_scale=True)

    with open(filename, "wb") as f:
        for chunk in response.iter_content(chunk_size=8192):
            progress_bar.update(len(chunk))
            f.write(chunk)

    progress_bar.close()


def load_ssl_model(ckpt_path="wav2vec_small.pt"):
    filepath = ckpt_path
    if not os.path.exists(filepath):
        download_file(WAV2VEC_URL, filepath)
    SSL_OUT_DIM = 768
    model, cfg, task = fairseq.checkpoint_utils.load_model_ensemble_and_task([filepath])
    ssl_model = model[0]
    ssl_model.remove_pretraining_modules()
    return SSL_model(ssl_model, SSL_OUT_DIM)


class BaselineLightningModule(pl.LightningModule):
    def __init__(self, cfg):
        super().__init__()
        self.cfg = cfg
        self.construct_model()
        self.save_hyperparameters()

    def construct_model(self):
        self.feature_extractors = nn.ModuleList(
            [load_ssl_model(ckpt_path="wav2vec_small.pt"), DomainEmbedding(3, 128),]
        )
        output_dim = sum([feature_extractor.get_output_dim() for feature_extractor in self.feature_extractors])
        output_layers = [LDConditioner(judge_dim=128, num_judges=3000, input_dim=output_dim)]
        output_dim = output_layers[-1].get_output_dim()
        output_layers.append(
            Projection(hidden_dim=2048, activation=torch.nn.ReLU(), range_clipping=False, input_dim=output_dim)
        )

        self.output_layers = nn.ModuleList(output_layers)

    def forward(self, inputs):
        outputs = {}
        for feature_extractor in self.feature_extractors:
            outputs.update(feature_extractor(inputs))
        x = outputs
        for output_layer in self.output_layers:
            x = output_layer(x, inputs)
        return x


class SSL_model(nn.Module):
    def __init__(self, ssl_model, ssl_out_dim) -> None:
        super(SSL_model, self).__init__()
        self.ssl_model, self.ssl_out_dim = ssl_model, ssl_out_dim

    def forward(self, batch):
        wav = batch["wav"]
        wav = wav.squeeze(1)  # [batches, audio_len]
        res = self.ssl_model(wav, mask=False, features_only=True)
        x = res["x"]
        return {"ssl-feature": x}

    def get_output_dim(self):
        return self.ssl_out_dim


class DomainEmbedding(nn.Module):
    def __init__(self, n_domains, domain_dim) -> None:
        super().__init__()
        self.embedding = nn.Embedding(n_domains, domain_dim)
        self.output_dim = domain_dim

    def forward(self, batch):
        return {"domain-feature": self.embedding(batch["domains"])}

    def get_output_dim(self):
        return self.output_dim


class LDConditioner(nn.Module):
    """
    Conditions ssl output by listener embedding
    """

    def __init__(self, input_dim, judge_dim, num_judges=None):
        super().__init__()
        self.input_dim = input_dim
        self.judge_dim = judge_dim
        self.num_judges = num_judges
        assert num_judges != None
        self.judge_embedding = nn.Embedding(num_judges, self.judge_dim)
        # concat [self.output_layer, phoneme features]

        self.decoder_rnn = nn.LSTM(
            input_size=self.input_dim + self.judge_dim,
            hidden_size=512,
            num_layers=1,
            batch_first=True,
            bidirectional=True,
        )  # linear?
        self.out_dim = self.decoder_rnn.hidden_size * 2

    def get_output_dim(self):
        return self.out_dim

    def forward(self, x, batch):
        judge_ids = batch["judge_id"]
        if "phoneme-feature" in x.keys():
            concatenated_feature = torch.cat(
                (x["ssl-feature"], x["phoneme-feature"].unsqueeze(1).expand(-1, x["ssl-feature"].size(1), -1)), dim=2
            )
        else:
            concatenated_feature = x["ssl-feature"]
        if "domain-feature" in x.keys():
            concatenated_feature = torch.cat(
                (concatenated_feature, x["domain-feature"].unsqueeze(1).expand(-1, concatenated_feature.size(1), -1),),
                dim=2,
            )
        if judge_ids != None:
            concatenated_feature = torch.cat(
                (
                    concatenated_feature,
                    self.judge_embedding(judge_ids).unsqueeze(1).expand(-1, concatenated_feature.size(1), -1),
                ),
                dim=2,
            )
            decoder_output, (h, c) = self.decoder_rnn(concatenated_feature)
        return decoder_output


class Projection(nn.Module):
    def __init__(self, input_dim, hidden_dim, activation, range_clipping=False):
        super(Projection, self).__init__()
        self.range_clipping = range_clipping
        output_dim = 1
        if range_clipping:
            self.proj = nn.Tanh()

        self.net = nn.Sequential(
            nn.Linear(input_dim, hidden_dim), activation, nn.Dropout(0.3), nn.Linear(hidden_dim, output_dim),
        )
        self.output_dim = output_dim

    def forward(self, x, batch):
        output = self.net(x)

        # range clipping
        if self.range_clipping:
            return self.proj(output) * 2.0 + 3
        else:
            return output

    def get_output_dim(self):
        return self.output_dim


2026-02-03 12:55:40 | INFO | fairseq.tasks.text_to_speech | Please install tensorboardX: pip install tensorboardX


In [18]:
utmos_model = UTMOSScore(device='cuda:0')  # Можно сменить на cpu

2026-02-03 12:55:42 | INFO | torch.distributed.nn.jit.instantiator | Created a temporary directory at /tmp/tmponykbwu6
2026-02-03 12:55:42 | INFO | torch.distributed.nn.jit.instantiator | Writing /tmp/tmponykbwu6/_remote_module_non_scriptable.py


In [19]:
val_df = pd.read_csv('files/langs_val_100texts.csv')

In [20]:
torch.set_num_threads(4)

results = []

for speaker in tqdm(model_ns.speakers):
    lang = speaker.split('_')[0]
    lang_df = val_df[val_df.lang==lang]
    for model_name, model in zip(['v5_cis_base_nostress', 'v5_cis_base'], [model_ns, model_s]):
        for text in lang_df.text.values:
            if lang in ['ru', 'ukr', 'bel'] or model_name=='v5_cis_base':
                text = accentors[lang_acc.get(lang, lang)](text)
            audio = model.apply_tts(text=text, speaker=speaker)
            utmos_score = utmos_model.score(audio.to(utmos_model.device)).mean().item()
            results.append({'lang': lang, 'lang_name': lang2name[lang], 'model_name': model_name, 'speaker': speaker, 'text': text, 'score': utmos_score})


100%|██████████████████████████████████████████████████████████████████████████████████████████████████| 60/60 [13:07<00:00, 13.12s/it]


In [21]:
val_df_v5 = pd.DataFrame(results)

In [22]:
val_df_v5.groupby(['model_name','lang_name'])['score'].agg(mean_with_moe)

model_name            lang_name           
v5_cis_base           Азербайджанский         2.18 ± 0.05
                      Армянский               3.11 ± 0.07
                      Башкирский              2.76 ± 0.04
                      Белорусский             3.03 ± 0.04
                      Грузинский              2.70 ± 0.07
                      Кабардино-Черкесский    2.57 ± 0.07
                      Казахский               2.94 ± 0.05
                      Калмыцкий               3.11 ± 0.05
                      Киргизский              2.86 ± 0.08
                      Мокшанский              3.23 ± 0.07
                      Русский                 3.04 ± 0.02
                      Таджикский              2.66 ± 0.05
                      Татарский               3.00 ± 0.05
                      Удмуртский              3.00 ± 0.06
                      Узбекский               3.00 ± 0.08
                      Украинский              3.26 ± 0.04
                      Хакасск

In [23]:
val_df_v5.groupby('model_name').score.agg(mean_with_moe)

model_name
v5_cis_base             2.95 ± 0.01
v5_cis_base_nostress    2.87 ± 0.01
Name: score, dtype: object

In [24]:
val_df_v5.groupby(['model_name','lang']).sample(100).groupby('model_name').score.agg(mean_with_moe)

model_name
v5_cis_base             2.89 ± 0.02
v5_cis_base_nostress    2.78 ± 0.02
Name: score, dtype: object

In [25]:
old_sp2lang = {'b_cv': 'chv',
 'cv_ekaterina': 'chv',
 'kz_M1': 'kaz',
 'kz_M2': 'kaz',
 'kz_F3': 'kaz',
 'kz_F1': 'kaz',
 'kz_F2': 'kaz',
 'b_tat': 'tat',
 'marat_tt': 'tat',
 'kalmyk_erdni': 'xal',
 'kalmyk_delghir': 'xal',
 'b_kalmyk': 'xal',
 'b_sah': 'sah',
 'b_udm': 'udm',
 'b_bashkir': 'bak',
 'b_uzb': 'uzb',
 'b_kjh': 'kjh',
 'mykyta': 'ukr',
 'b_ru': 'ru'
 }

In [26]:
old_results = []

for speaker in tqdm(old_model.speakers):
    if speaker not in old_sp2lang:
        continue
    lang = old_sp2lang[speaker]
    lang_df = val_df[val_df.lang==lang]
    for model_name, model in zip(['v4'], [old_model]):
        for text in lang_df.text.values:
            audio = model.apply_tts(text=text, speaker=speaker)
            utmos_score = utmos_model.score(audio.to(utmos_model.device)).mean().item()
            old_results.append({'lang': lang, 'lang_name': lang2name[lang], 'model_name': model_name, 'speaker': speaker, 'text': text, 'score': utmos_score})

100%|██████████████████████████████████████████████████████████████████████████████████████████████████| 31/31 [02:48<00:00,  5.44s/it]


In [27]:
val_df_v4 = pd.DataFrame(old_results)

In [28]:
val_df_v4.groupby(['model_name','lang_name'])['score'].agg(mean_with_moe)

model_name  lang_name 
v4          Башкирский    1.68 ± 0.05
            Казахский     1.65 ± 0.02
            Калмыцкий     1.66 ± 0.03
            Русский       1.90 ± 0.06
            Татарский     1.82 ± 0.05
            Удмуртский    2.03 ± 0.05
            Узбекский     1.78 ± 0.06
            Хакасский     1.76 ± 0.05
            Чувашский     1.75 ± 0.04
            Якутский      1.62 ± 0.04
Name: score, dtype: object

In [29]:
val_df_v4.groupby('model_name').score.agg(mean_with_moe)

model_name
v4    1.73 ± 0.01
Name: score, dtype: object

In [30]:
val_df_v4.groupby(['lang']).sample(100).groupby('model_name').score.agg(mean_with_moe)

model_name
v4    1.76 ± 0.02
Name: score, dtype: object

# Дополнительные проверки

## Максимальная длина текста

In [31]:
val_df = pd.read_csv('files/langs_val_100texts.csv')

In [32]:
dfs = []
for i in range(4, 20):
    joined = (
        val_df.groupby('lang_name')[['text', 'lang_name']].sample(i)
        .groupby('lang_name')
        .agg(lambda x: ', '.join(x))
    ).reset_index()
    joined['text'] = joined['text'].apply(lambda x: x.replace('.', ',').replace('?', ',').replace('!', ','))
    dfs.append(joined)

joined = pd.concat(dfs)
joined['text_len'] = joined['text'].apply(len)

In [33]:
joined.describe()

text_len
count   320.000000
mean    640.446875
std     291.745289
min      73.000000
25%     403.750000
50%     621.500000
75%     853.000000
max    1351.000000

In [34]:
passed = []
with tqdm(total=len(joined)) as pbar:
    for i, row in joined.iterrows():
        try:
            _ = model_ns.apply_tts(row['text'],
                                   speaker=random.choice(lang2speakers[row['lang_name']]))
            passed.append(1)
        except Exception as e:
            passed.append(0)
            
        pbar.update(1)

100%|████████████████████████████████████████████████████████████████████████████████████████████████| 320/320 [02:09<00:00,  2.47it/s]


In [35]:
joined['passed'] = passed

In [36]:
joined[joined.passed==0].groupby('lang_name')['text_len'].min()

lang_name
Азербайджанский     828
Армянский          1104
Башкирский          912
Белорусский         704
Грузинский          769
Казахский           925
Калмыцкий           623
Киргизский          938
Мокшанский         1111
Русский            1115
Таджикский          775
Татарский           860
Удмуртский         1036
Узбекский           909
Украинский          712
Хакасский           793
Чувашский           926
Эрзянский          1016
Якутский            930
Name: text_len, dtype: int64

## Проверка алфавита поддерживаемых символов

In [37]:
assert model_ns.symbols == model_s.symbols
# Основные символы
model_ns.symbols

"|!'+,-.:;?hабвгдежзийклмнопрстуфхцчшщъыьэюяёєіїјўґғҕҗҙқҝҡңҥҫүұҳҷҹһӑӗәӝӟӣӥӧөӯӱӳӵӏ—… "

In [38]:
# Дополнительные символы
# Все дополнительные символы с помощью словарей переводятся в расширенную кириллицу перед подачей в модель
# Азербайджанский и узбекский поддерживают нативную расширенную кириллицу

for lang, sup_symbols in model_ns.packages[0].ext_alph.items():
    print(lang2name[lang], ', '.join(sup_symbols.keys()))

Грузинский ა, ბ, გ, დ, ე, ვ, ზ, ჱ, თ, ი, კ, ლ, მ, ნ, ჲ, ო, პ, ჟ, რ, ს, ტ, ჳ, უ, ფ, ქ, ღ, ყ, შ, ჩ, ც, ძ, წ, ჭ, ხ, ჴ, ჯ, ჰ, ჵ
Армянский ա, բ, գ, դ, ե, զ, է, ը, թ, ժ, ի, լ, խ, ծ, կ, հ, ձ, ղ, ճ, մ, յ, ն, շ, ո, չ, պ, ջ, ռ, ս, վ, տ, ր, ց, ւ, փ, ք, օ, ֆ
Азербайджанский a, b, c, ç, d, e, ə, f, g, ğ, h, x, i, i̇, j, k, q, l, m, n, o, ö, p, r, s, ş, t, u, ü, v, y, z
Узбекский a, b, d, e, f, g, h, i, j, k, l, m, n, o, p, q, r, s, t, u, v, x, y, z, o', g', sh, ch, ng, '


## Cписок доступных дикторов

In [39]:
assert model_ns.speakers == model_s.speakers
sorted(model_ns.speakers)

['aze_gamat',
 'bak_aigul',
 'bak_alfia',
 'bak_alfia2',
 'bak_miyau',
 'bak_ramilia',
 'bel_anatoliy',
 'bel_dmitriy',
 'bel_larisa',
 'chv_ekaterina',
 'erz_alexandr',
 'hye_zara',
 'kat_vika',
 'kaz_zhadyra',
 'kaz_zhazira',
 'kbd_eduard',
 'kir_nurgul',
 'kjh_karina',
 'kjh_sibday',
 'mdf_oksana',
 'ru_aigul',
 'ru_albina',
 'ru_alexandr',
 'ru_alfia',
 'ru_alfia2',
 'ru_bogdan',
 'ru_dmitriy',
 'ru_eduard',
 'ru_ekaterina',
 'ru_gamat',
 'ru_igor',
 'ru_karina',
 'ru_kejilgan',
 'ru_kermen',
 'ru_marat',
 'ru_miyau',
 'ru_nurgul',
 'ru_oksana',
 'ru_onaoy',
 'ru_ramilia',
 'ru_roman',
 'ru_safarhuja',
 'ru_saida',
 'ru_sibday',
 'ru_vika',
 'ru_zara',
 'ru_zhadyra',
 'ru_zhazira',
 'ru_zinaida',
 'sah_zinaida',
 'tat_albina',
 'tat_marat',
 'tgk_onaoy',
 'tgk_safarhuja',
 'udm_bogdan',
 'ukr_igor',
 'ukr_roman',
 'uzb_saida',
 'xal_kejilgan',
 'xal_kermen']

In [40]:
speakers2lang = {s: s.split('_')[0] for s in model_ns.speakers}

lang2speakers = {}
for speaker, lang in speakers2lang.items():
    lang_name = lang2name[lang]
    (lang2speakers.setdefault(lang_name, [])).append(speaker)
lang2speakers

{'Башкирский': ['bak_aigul',
  'bak_alfia',
  'bak_alfia2',
  'bak_miyau',
  'bak_ramilia'],
 'Русский': ['ru_aigul',
  'ru_albina',
  'ru_alexandr',
  'ru_alfia',
  'ru_alfia2',
  'ru_bogdan',
  'ru_dmitriy',
  'ru_ekaterina',
  'ru_vika',
  'ru_gamat',
  'ru_igor',
  'ru_karina',
  'ru_kejilgan',
  'ru_kermen',
  'ru_marat',
  'ru_miyau',
  'ru_nurgul',
  'ru_oksana',
  'ru_onaoy',
  'ru_ramilia',
  'ru_roman',
  'ru_safarhuja',
  'ru_saida',
  'ru_sibday',
  'ru_zara',
  'ru_zhadyra',
  'ru_zhazira',
  'ru_zinaida',
  'ru_eduard'],
 'Татарский': ['tat_albina', 'tat_marat'],
 'Эрзянский': ['erz_alexandr'],
 'Белорусский': ['bel_anatoliy', 'bel_dmitriy', 'bel_larisa'],
 'Удмуртский': ['udm_bogdan'],
 'Чувашский': ['chv_ekaterina'],
 'Грузинский': ['kat_vika'],
 'Азербайджанский': ['aze_gamat'],
 'Украинский': ['ukr_igor', 'ukr_roman'],
 'Хакасский': ['kjh_karina', 'kjh_sibday'],
 'Калмыцкий': ['xal_kejilgan', 'xal_kermen'],
 'Киргизский': ['kir_nurgul'],
 'Мокшанский': ['mdf_oksana'],